In [75]:
import pandas as pd
import altair as alt
import numpy as np
import re

# Imports for reading FRED API
from os import environ
from io import BytesIO
from zipfile import ZipFile
from urllib.request import urlopen

try:
    # for local execution
    apiKeyFromFile = open("/Users/kyledunn/fredApiKey.txt", "r").read().strip()
except FileNotFoundError:
    apiKeyFromFile = None
    pass
# for CI
apiKey = environ.get("FRED_API_KEY", apiKeyFromFile)

def getSeries(series="", apiKey=apiKey, description=None):
    # Construct URL template, fetching as much data as possible
    fetchCommand = "https://api.stlouisfed.org/fred/series/observations?series_id={s}&realtime_end=9999-12-31&api_key={k}&file_type=txt" 
    
    # Call the FRED API
    resp = urlopen(fetchCommand.format(s=series, k=apiKey))
    
    # Read and extract the data from the Zipfile response
    zipfile = ZipFile(BytesIO(resp.read()))
    filesInZip = zipfile.namelist()
    data = zipfile.open(filesInZip[1])
    
    if description is None:
        description = series
    
    # Make a well-formed dataframe
    df = pd.read_csv(data, sep="\t", header=None, skiprows=1,
                       names=["date", description, "rt_start", "rt_end"], na_values=".")
    
    df['date'] = pd.to_datetime(df.date)
    
    return df.set_index("date")

df_cpi = getSeries("CWUR0000SA0")

In [76]:
# Encode the monthly retail sales column names
yearColumns = lambda y : map(lambda s: s.format(y), ['Jan. {}', 'Feb. {}', 'Mar. {}', 'Apr. {}', 'May {}', 'Jun. {}', 'Jul. {}', 'Aug. {}', 'Sep. {}', 'Oct. {}', 'Nov. {}', 'Dec. {}', 'Total {}'])
standardColumns = lambda y : ['NAICS', 'Description'] + list(yearColumns(y))

# Note, need to add to 2019 as new data is released
# TODO, try to automate this better
oneOffYears = {
    '2019': standardColumns('2019')[:2] + ['Jan. 2019', 'Feb. 2019', 'Mar. 2019', 'Apr. 2019', 'May 2019', 'Jun. 2019', 'Jul. 2019', 'Aug. 2019', 'Sep. 2019', 'Oct. 2019', 'Nov. 2019', '2019 CUM', '2019 PY CUM'],
    '2016': standardColumns('2016') + ['IGNORE']
}

# Fetch the historical monthly retail sales data
# set sheet_name to none to read all sheets in the XLS
dfs = pd.read_excel('https://www.census.gov/retail/mrts/www/mrtssales92-present.xls', sheet_name=None)

# parse the results sheet-by-sheet, normalizing the columns names and index
allDfs = []
for y in dfs.keys():
    #print(dfs[y].columns)
    dfs[y].columns = oneOffYears.get(y) or standardColumns(y)
    dfs[y] = dfs[y].drop('NAICS', axis=1)
    #print(dfs[y].iloc[5:109].set_index('Description').index.is_unique)
    allDfs.append(dfs[y].iloc[5:109].set_index('Description'))

# workaround for merging the sheets into a single dataframe
old = pd.concat(allDfs[2:], axis=1)
new = pd.concat(allDfs[:2], axis=1)
combined = new.join(old).drop('ADJUSTED(2)').T

#combined.head(10)

In [77]:
# subset the combined dataset to the monthly report records
tsNormalized = combined[combined.index.map(lambda v: re.search('[A-z]{3}.? \d{4}$', v) is not None and 'Total' not in v)].copy()

# create a proper datetime column
# note: (p) "preliminary" records lose their designation and are treated the same as final records
tsNormalized['dt'] = tsNormalized.index.map(lambda v: pd.to_datetime(v.replace('(p)', ''), format='%b. %Y') 
                                            if '.' in v else pd.to_datetime(v, format='%b %Y'))

# reindex the dataframe on the datetime field and ensure all values are numeric
dt = tsNormalized.set_index('dt')
dt = dt.apply(pd.to_numeric, errors='coerce')
#dt.head()

# Melt and re-aggregate to combine duplicate categories
df_melted = dt.reset_index().melt(id_vars='dt')
df_agg = df_melted.groupby(['dt', 'Description']).agg(sum).reset_index('Description')
#df_agg.head()

# Reshape the dataframe so each monhtly report is a row and each category is a column
df_combined = df_agg.pivot(index=df_agg.index, columns='Description')
df_combined.columns = df_combined.columns.droplevel()
#df_combined.tail()

## Monthly Retail Trade Report

---

### What is the trend for home furnishing retail stores?

In [78]:
def doLineChartFor(metric, df, yLabel='Monthly Revenue [Million USD]', color='purple'):
    return alt.Chart(df.reset_index()).mark_line(color=color).encode(
        alt.X('dt', axis=alt.Axis(title='')),
        alt.Y('{}:Q'.format(metric), axis=alt.Axis(title=yLabel)),
        tooltip=[alt.Tooltip('dt:T'), alt.Tooltip('{}:Q'.format(metric))]
    ).properties(
        title='US: {} - over time'.format(metric),
        height=500,
        width=750
    )
    
doLineChartFor('Furniture, home furn, electronics, and appliance stores', df_combined)

alt.Chart(...)

### What is the *growth* trend for home furnishing retail stores?

In [79]:
def doYoYChartFor(metric, df, color=''):
    yoy = df[[metric]].pct_change(12).apply(lambda v: v*100.).sort_index()

    return alt.Chart(yoy[-160:].reset_index()).mark_bar(size=2.5).encode(
        alt.X('dt:T', axis=alt.Axis(title='')),
        alt.Y('{}:Q'.format(metric), axis=alt.Axis(title='Year over Year Revenue Growth [%]'.format(metric))),
        tooltip=[alt.Tooltip('dt:T'), alt.Tooltip('{}:Q'.format(metric))]
    ).properties(
        title='US: {} - growth over time'.format(metric),
        height=500,
        width=750
    )
    
doYoYChartFor('Furniture, home furn, electronics, and appliance stores', df_combined)

alt.Chart(...)

### What is the trend for retail sales revenue?

In [80]:
doLineChartFor('Retail sales, total', df_combined, 'Monthly Revenue [Million USD]')

alt.Chart(...)

### What is the *growth* trend for retail sales revenue?

In [81]:
doYoYChartFor('Retail sales, total', df_combined)

alt.Chart(...)

### What is the *growth* trend for automotive-related retail sales revenue?

In [82]:
as_yoy = df_combined.copy()

# Compute auto-related sales revenues by ( total - (total - autos) ) => autos
as_yoy['Automotive Related'] = (as_yoy['Retail sales, total'] -\
                   as_yoy['Retail sales, total (excl. motor vehicle and parts dealers)'])

as_df = as_yoy['Automotive Related'].reset_index()

doYoYChartFor('Automotive Related', as_df.set_index('dt'))

alt.Chart(...)

### How do the above trends look when adjusting for inflation (CPI)?

In [83]:
toCompare = [
    'Retail sales, total',
    'Retail sales, total (excl. motor vehicle and parts dealers)',
    'Retail sales and food services excl motor vehicle and parts'
]

tmp = df_combined[['Retail sales, total', 'Retail sales, total (excl. motor vehicle and parts dealers)']].copy()
tmp.columns = ['Retail sales, total', 'Retail sales excluding motor vehicles']

tmp['Retail sales, motor vehicles and parts'] = tmp['Retail sales, total'] - tmp['Retail sales excluding motor vehicles']
tmp = tmp.join(df_cpi['CWUR0000SA0'])
tmp.columns = ['Retail Total', 'Retail Excluding Motor Vehicles', 'Retail Motor Vehicles', 'CPI']

tmp['Total-adj'] = tmp['Retail Total'] / tmp['CPI']
tmp['Auto-adj'] = tmp['Retail Motor Vehicles'] / tmp['CPI']

chartable = tmp.reset_index()[['index', 'Total-adj', 'Auto-adj']].melt(id_vars='index')

alt.Chart(chartable).mark_line().encode(
    alt.X('index:T', axis=alt.Axis(title='')),
    alt.Y('value:Q', axis=alt.Axis(title='Monthly Revenue [Million 1982-1984 USD]')),
    alt.Color('variable:N')
).properties(
    title='US: CPI-adjusted Retail Sales Revenue',
    height=500,
    width=700
)

alt.Chart(...)

### What is the *growth* trend for retail sales when adjusted for inflation (CPI)?

In [84]:
df_adj = tmp['Total-adj'].reset_index().copy()
df_adj.columns = ['dt', 'Retail Sales Adj']

doYoYChartFor('Retail Sales Adj', df_adj.set_index('dt'))

alt.Chart(...)

### What is the trend for non-store retailers (ecommerce)?

In [85]:
doLineChartFor('Nonstore retailers', df_combined)

alt.Chart(...)

## Manufacturing

---

In [86]:
dfm = pd.read_excel('https://www.census.gov/manufacturing/m3/prel/historical_data/histshts/naics/naicsnop.xls', header=None)
dfm.columns = ['Code', 'Year', 'Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
dfm = dfm.set_index('Year')

#dfm.loc[2019].head()

In [87]:
dfm_release = pd.read_excel('https://www.census.gov/manufacturing/m3/reldates.xls', skiprows=3).iloc[:-3]
#dfm_release.tail(14)

In [88]:
# Code defs: https://www.census.gov/manufacturing/m3/historical_data/naicshist.pdf

subset = dfm[dfm.Code == 'UMTMNO'].drop('Code', axis=1).reset_index()
melted = subset.melt(id_vars=['Year'])
melted['dt'] = pd.to_datetime(melted['Year'].astype(str) + melted['variable'], format='%Y%b')

In [89]:
alt.Chart(melted.sort_values('dt')).mark_line(color='indigo').encode(
    alt.X('dt', axis=alt.Axis(title='')),
    alt.Y('value:Q', axis=alt.Axis(title='Monthly Revenue [Million USD]')),
    tooltip=[alt.Tooltip('value:Q'), alt.Tooltip('dt:T', format='%B - %Y')]
).properties(
    title='New US Manufacturing Orders (unadjusted, excluding defense)',
    height=450,
    width=750,
)

alt.Chart(...)

In [90]:
yoy_orders = melted.set_index('dt')['value'].sort_index().dropna()\
             .pct_change(12).apply(lambda v: v * 100.).reset_index()

alt.Chart(yoy_orders[-150:]).mark_bar(color='blue', size=2.5).encode(
    alt.X('dt', axis=alt.Axis(title='')),
    alt.Y('value:Q', axis=alt.Axis(title='Year over Year Revenue Growth [%]')),
    tooltip=[alt.Tooltip('dt:T', format='%B - %Y', title='Period'), alt.Tooltip('value:Q', title='% Change')]
).properties(
    title='New US Manufacturing Order Growth (unadjusted, excluding defense)',
    height=450,
    width=750,
    background="white"
)

alt.Chart(...)

## New Construction

---

In [91]:
dfc_release = pd.read_html('https://www.census.gov/construction/c30/release.html')[0]
#dfc_release.head()

In [92]:
# https://www.census.gov/construction/c30/release.html

dfc = pd.read_excel('https://www.census.gov/construction/c30/xls/totsatime.xls', skiprows=3).iloc[:311]

dfc['dt'] = dfc.Date.map(lambda d:
                         pd.to_datetime(d, format='%b-%y') if d[-1] not in ['r', 'p'] 
                         else pd.to_datetime(d[:-1], format='%b-%y'))

In [93]:
alt.Chart(dfc).mark_line(color='indigo').encode(
    alt.X('dt', axis=alt.Axis(title='Year')),
    alt.Y('Total\n\rConstruction1:Q', axis=alt.Axis(title='Monthly Spending [Million USD]')),
    tooltip=[alt.Tooltip('dt:T', format='%B - %Y', title='Period'), alt.Tooltip('Total\n\rConstruction1:Q', title='% Change')]
).properties(
    title='New US Construction Spending (unadjusted)',
    height=450,
    width=750,
)

alt.Chart(...)

In [94]:
yoy_construction = dfc.set_index('dt')['Total\n\rConstruction1'].sort_index().dropna()\
                   .pct_change(12).apply(lambda v: v * 100.).reset_index()


alt.Chart(yoy_construction).mark_bar(width=1.5).encode(
    alt.X('dt', axis=alt.Axis(title='')),
    alt.Y('Total\n\rConstruction1:Q', axis=alt.Axis(title='Year over year spending growth [%]')),
    tooltip=[alt.Tooltip('dt:T', format='%B - %Y', title='Period'), alt.Tooltip('Total\n\rConstruction1:Q', title='% Change')]
).properties(
    title='New US Construction Spending Growth (unadjusted)',
    height=450,
    width=750,
    background="white"
)

alt.Chart(...)

## Quarterly Services Survey

---

In [95]:
# https://www.census.gov/services/qss/historic_data.html

urlFor = lambda y, q: 'http://www2.census.gov/services/qss/{0}/all_{0}q{1}.xls'.format(y, q) if y < 2019\
                 else 'http://www2.census.gov/services/qss/{0}/all_{0}Q{1}.xls'.format(y, q)

# [1:] -> omit Q1 2004, :-1 -> omit Q4 2019
urls = [(urlFor(y, q), y, q) for y in range(2004, 2020) for q in range(1, 5)][1:-1]

# TODO - try to automate this
# Manually append the most recent reporting period
#urls = urls + [('https://www.census.gov/services/qss/qss-current.xls', 2019, 1)]

In [96]:
%%time

# Depending on the year and quarter, the most useful sheet name 
# evolves from table1 -> table1B -> table1b -> tableA1
def sheetNameFor(y, q):
    if y <= 2007:
        return 'table1-{0}Q{1}'.format(y, q)
        
    elif y == 2008 and q != 4:
        if q != 4:
            return 'table1-{0}Q{1}'.format(y, q)
        else:
            return 'table1B-{0}Q{1}'.format(y, q)
            
    elif y < 2016:
        return 'table1B-{0}Q{1}'.format(y, q)
      
    elif y == 2016:
        if q != 4:
            return 'table1B-{0}Q{1}'.format(y, q)
        else:
             return 'table1b-{0}Q{1}'.format(y, q)
    else:
        return 'table1b-{0}Q{1}'.format(y, q)

rest = list(map(lambda u: (u[1], u[2], pd.read_excel(u[0], sheet_name=sheetNameFor(u[1], u[2]))), urls))

CPU times: user 6.24 s, sys: 415 ms, total: 6.65 s
Wall time: 1min 31s


In [97]:
# Depending on the year and quarter, we need to skip differing numbers of "header" rows
def indexFor(y, q):
    if y < 2006:
        return 6
    elif y == 2006 and q < 2:
        return 6
    else:
        return 4

revenues = list(map(lambda d: (d[0], d[1], d[2].iloc[indexFor(d[0], d[1]):, 0:8]), rest))

In [98]:
%%time

# To make the various NAICS codes align, we have to cleanup certain codes and mark aggregate categories accordingly
def remapCategory(code):
    if 'pt' in code:
        return re.sub('[^\d]+', '', code) + 'pt'
    elif code in ['11', '21', '22', '23', '31-33', '42', '44-45', '48-49', '51', '52', '53',\
                '54', '55', '56', '61', '62', '71', '72', '81', '92']:
        return code + 'c'
    else:
        return code

cleanIt = lambda s: re.sub('(,$|,\sand.*$)', '', re.sub('\s?\(.*$', '', re.sub('\s*\d+$', '', re.sub('\s+', ' ', s.replace('…', '').replace('.', '').strip()))))

# Depending on the year and quarter we need to provide consistent column headers looking back in time from current
def getPrevious(y, q):
    if q == 1:
        return ['{}Q1'.format(y)] + ['{0}Q{1}'.format(y-1, n+1) for n in reversed(range(4))]
    elif q == 2:
        return ['{}Q2'.format(y)] + ['{}Q1'.format(y)] + ['{0}Q{1}'.format(y-1, n+1) for n in reversed(range(4))][:-1]
    elif q == 3:
        return ['{}Q3'.format(y)] + ['{}Q2'.format(y)] + ['{}Q1'.format(y)] + ['{0}Q{1}'.format(y-1, n+1) for n in reversed(range(4))][:-2]
    elif q == 4:
        return ['{0}Q{1}'.format(y, n+1) for n in reversed(range(4))] + ['{}Q4'.format(y-1)]

crevs = []
for y, q, df in revenues:
    tmp = df.copy()
    tmp.columns = ['Code', 'Business', '{0}Q{1}YTD'.format(y, q)] + getPrevious(y, q)
    tmp['Source'] = tmp.Code.map(lambda c: "{0}Q{1}".format(y, q))
    
    tmp = tmp[pd.notnull(tmp.Business)]
    tmp = tmp[pd.notna(tmp.Business)]
    tmp = tmp[pd.notnull(tmp.Code)]

    # Exclude records reporting "previous definitions"
    tmp = tmp[tmp.Code.map(lambda c: '*' not in str(c))]

    tmp['Code'] = tmp.Code.map(lambda s: remapCategory(str(s)))

    tmp['Business'] = tmp['Business'].map(lambda s: cleanIt(s) if isinstance(s, str) else s)
    
    crevs.append(tmp.set_index('Code').T)

# Combine the revised dataframes into one
catrevs = pd.concat(crevs, sort=False)

# Use the first valid identifier as the new column header
codeLut = {}
for c in catrevs.columns:
    codeLut[c] = catrevs[c].loc['Business'].dropna().iloc[0]

# Apply categories markers to each code for aggregation
catrevs.columns = list(map(lambda v: codeLut.get(v) + ' ' + v, catrevs.columns))

catrevs = catrevs[catrevs.index.map(lambda v: v[-3:] != 'YTD' and v not in ['Source', 'Business'])]

catrevs = catrevs[~catrevs.index.isin(['2003Q2', '2003Q3'])]

catrevs = catrevs.apply(pd.to_numeric, errors='coerce')
catrevs['dt'] = catrevs.index.map(pd.to_datetime)

revfinal = catrevs.set_index('dt')
#revfinal.tail(15)

CPU times: user 1.5 s, sys: 7.13 ms, total: 1.51 s
Wall time: 1.51 s


In [99]:
# print out the categories
cats = [c for c in revfinal.columns if 'c' in c[-1]]
#cats

In [100]:
#revfinal.tail(30)

### What is the revenue trend compared accross industries?

In [119]:
# Melt and re-aggregate to combine preliminary and final revisions (via average)
tmp = revfinal[cats].reset_index().melt(id_vars=['dt']).copy()
categories_agg = tmp.groupby(['dt', 'variable']).agg(np.mean).reset_index()

alt.Chart(categories_agg).mark_line().encode(
    alt.X('dt', axis=alt.Axis(title=None)),
    alt.Y('value:Q', axis=alt.Axis(title='Quarterly Revenues [Million USD]')),
    alt.Color('variable:N', title="NAICS Group")
).properties(
    title="Quarterly Revenues by NAICS category (Census Quarterly Services Survey)",
    background="white",
    width=750,
    height=450
)

alt.Chart(...)

### What proportion of total reported revenues is each industry?

In [120]:
alt.Chart(categories_agg).mark_bar().encode(
    alt.X('dt:T', axis=alt.Axis(title=None)),
    alt.Y('value:Q', axis=alt.Axis(title='Quarterly Revenues [Million USD]')),
    alt.Color('variable:N', title="NAICS Group")
).properties(
    title="Quarterly Revenues by NAICS category (Census Quarterly Services Survey)",
    background="white",
    width=750,
    height=450
)

alt.Chart(...)

In [103]:
# TODO:

# - Correct these values for inflation
# - Try to correlate tax revenues per sector with each sectors' contribution to GDP

In [126]:
categories_agg.tail()

dt                                variable     value
699 2019-07-01                      Other services 81c  144608.0
700 2019-07-01            Professional, scientific 54c  510620.0
701 2019-07-01  Real estate and rental and leasing 53c  187554.0
702 2019-07-01   Transportation and warehousing 48-49c  254266.0
703 2019-07-01                           Utilities 22c  135670.0

In [127]:
df_ppi.head()

PPIACO    rt_start rt_end
date                                 
1913-01-01    12.1  1999-08-13    NaN
1913-02-01    12.0  1999-08-13    NaN
1913-03-01    12.0  1999-08-13    NaN
1913-04-01    12.0  1999-08-13    NaN
1913-05-01    11.9  1999-08-13    NaN

In [124]:
df_cpi = getSeries("CWUR0000SA0", apiKey)
df_ppi = getSeries("PPIACO", apiKey)

def adjustValueWithDate(val, date):
    valOrVals = (val / (df_ppi.iloc[df_ppi.index.get_loc(pd.to_datetime(date))]['PPIACO'] / 100.))
    return valOrVals if isinstance(valOrVals, np.float64) else valOrVals[-1]

adj_categories_agg = pd.DataFrame.from_records([(dt, variable, value, adjustValueWithDate(value, dt))
                                                for ix, dt, variable, value in categories_agg.itertuples()])
adj_categories_agg.columns = ['dt', 'variable', 'value', 'value_adj']

### What is the inflation-adjusted revenue trend compared accross industries?

In [121]:
alt.Chart(adj_categories_agg).mark_line().encode(
    alt.X('dt', axis=alt.Axis(title=None)),
    alt.Y('value_adj:Q', axis=alt.Axis(title='Quarterly Revenues [Million 1982-1984 USD]')),
    alt.Color('variable:N', title="NAICS Group")
).properties(
    title="Quarterly Revenues by NAICS category (Census Quarterly Services Survey, CPI-adjusted)",
    width=750,
    height=450
)

alt.Chart(...)

In [111]:
def getEmploymentSeries(seriesId="CEU5500000001", name="financial activities"):
    # Finance and insurance
    url = 'https://data.bls.gov/timeseries/{}?amp%222bdata_tool=XGtable&output_view=data&from_year=1990&to_year=2019'
    furl = url.format(seriesId)
    #print(furl)
    df_employment = pd.read_html(furl)[1]
    #print(df_employment.head())
    df_employment.columns = ['Year'] + df_employment.columns.tolist()[1:]
    
    df_emp = df_employment.iloc[:, :-1].melt(id_vars='Year')

    df_emp = df_emp[df_emp.Year != 'P : preliminary']

    df_emp['Date'] = pd.to_datetime(df_emp['variable'] + " " + df_emp['Year'], format="%b %Y")
    df_emp[name] = pd.to_numeric(df_emp['value'], errors='coerce')
    
    #print(df_emp.head(1))
    
    return df_emp[['Date', name]].sort_values('Date').set_index('Date').copy()

dfs_employment = []

industries = {
    'goods-producing': 'CEU0600000001',
    'mining and logging': 'CEU1000000001',
    'construction': 'CEU2000000001',
    'manufacturing': 'CEU3000000001',
    'retail trade': 'CEU4200000001',
    'transportation and warehousing': 'CEU4300000001',
    'information': 'CEU5000000001',
    'financial activities': 'CEU5500000001',
    'professional services': 'CEU6000000001',
    'education and health': 'CEU6500000001',
    'government': 'CEU9000000001'
}

for i in industries.keys():
    dfs_employment.append(getEmploymentSeries(industries[i], i))
    
df_employment = pd.concat(dfs_employment, axis=1)

exclude = [
    'Adminstrative and support and waste management 56c',
    'Arts, entertainment 71c',
    'Other services 81c',
    'Utilities 22c',
    'Real estate and rental and leasing 53c',
    'Educational services 61c'
]

def computeDollarsPerCapita(val, variable, date):
    if variable == 'Information 51c':
        return val / df_employment.iloc[df_employment.index.get_loc(pd.to_datetime(date), method='nearest')]['information']
    elif variable == 'Finance and insurance 52c':
        return val / df_employment.iloc[df_employment.index.get_loc(pd.to_datetime(date), method='nearest')]['financial activities']
    elif variable == 'Health care and social assistance 62c':
        return val / df_employment.iloc[df_employment.index.get_loc(pd.to_datetime(date), method='nearest')]['education and health']
    elif variable == 'Professional, scientific 54c':
        return val / df_employment.iloc[df_employment.index.get_loc(pd.to_datetime(date), method='nearest')]['professional services']
    elif variable == 'Transportation and warehousing 48-49c':
        return val / df_employment.iloc[df_employment.index.get_loc(pd.to_datetime(date), method='nearest')]['transportation and warehousing']

revenue_per_employee = pd.DataFrame.from_records([(dt, variable, value, computeDollarsPerCapita(value_adj, variable, dt))
                                                for ix, dt, variable, value, value_adj in adj_categories_agg[~adj_categories_agg.variable.isin(exclude)].itertuples()])

revenue_per_employee.columns = ['dt', 'variable', 'value', 'value_adj']

### What is the inflation-adjusted revenue per employee trend compared across industries?

In [122]:
alt.Chart(revenue_per_employee).mark_line().encode(
    alt.X('dt', axis=alt.Axis(title=None)),
    alt.Y('value_adj:Q', axis=alt.Axis(title='Quarterly Revenues per Employee [Million USD]')),
    alt.Color('variable:N', title='NAICS Group')
).properties(
    title="Quarterly Revenues per Employee by NAICS category (Census Quarterly Services Survey, CPI-adjusted)",
    background="white",
    width=750,
    height=450
)

alt.Chart(...)